# Projeto 06- Bigdata - Spark

## Contextualização

A PyCoders Ltda., cada vez mais especializada no mundo da Engenharia de Dados, foi procurada por uma fintech para desenvolver um projeto de análise de dados.

A fintech percebeu que muito dos seus processos estão se tornando lentos pelo uso incorreto de ferramentas! Desde que está se trabalhando com Big Data, uso de bibliotecas como pandas e sklearn tornam a Extracção, Tratamento e Carregamento dos dados (ETL) processos muito lentos, inclusive o treinamento de modelos de machine learning (ML) tem se tornado um processo muito demorado.

Para lidar com esse problema, foi sugerido fazer uso da biblioteca pyspark, para implementar todo o fluxo de ETL.


## Objetivo de projeto

Como queremos demostrar que de fato a solução proposta traz uma melhora, foi solicitado implementar uma análise comparativa de resultados usando a antiga abordagem (usando pandas e sklearn) e usando a nova proposta de solução (pyspark). Para isso, tome em consideração o seguinte:

1. Escolha dois conjuntos de dados interessantes, sendo que um deles é pequeno (menos de 10.000 linhas) e o outro bem maior (acima de 1.000.000 linhas). Uma possivel sugestão seria usar um unico dataset (com muitos dados), e extrair uma pequena proporção dos dados desde dataset e considerar essa parte como o dataset menor.

   - **Sugestão:** <a href="https://www.kaggle.com/datasets/computingvictor/transactions-fraud-datasets" target="_blank">Transactions Fraud Dataset</a>.

2. Aplique todas as etapas de ETL nos dois conjuntos de dados usando pandas y pyspark. As etapas incluem: (1) Extração dos dados, por exemplo de um csv, (2) Tratamento dos dados (limpeza, alteração de nomes de colunas, criação de mais tabelas, transformação nas colunas, etc.), e, (3) Carregamento dos dados (salvar a transformação feita sobre os dados). 

3. Lembre que cada etapa tem que ser feita usando unicamente pandas/sklearn ou pyspark.

4. Como o objetivo é fazer uma análise comparativa, tome em consideração o tempo que demora cada etapa, para depois facilitar as comparações. 

Boa sorte e divirta-se!!

## Datasets


Você pode procurar conjuntos de dados aqui:

1. No repositório da <a href="https://archive.ics.uci.edu/ml/datasets.php" target="_blank">UCI</a>.
1. No <a href="https://www.kaggle.com/datasets" target="_blank">Kaggle</a>.


## Organização e entregáveis

1. O projeto pode ser feito em grupo de até 05 participantes.
2. O projeto completo (Notebook, código-fonte, link para fontes, bases e demais artefatos) deve ser enviado por e-mail ``jchambyd@gmail.com`` com nome dos participantes. Colocar no assunto do e-mail: ``Projeto Santander Coders 2024 - Data - Turma 1180``

## Deadline
**Apresentação**: 10/12/2024 <br>


## Exemplo:

[ETL simples usando pandas][1]

[ETL simples usando pyspark][2]

[1]: https://blog.devgenius.io/basic-etl-using-pandas-23729ae4e05e

[2]: https://blog.devgenius.io/basic-etl-using-pyspark-ed08b7e53cf4

### ETL PySpark

#### 1. Extração e exploração de dados

In [0]:
from pyspark.sql.functions import col,regexp_replace
from datetime import timedelta
import time


In [0]:
#contagem tempo de execução da  extração
start_time_extraction = time.time()

In [0]:

usersCsvPath = "dbfs:/FileStore/transactions_data.csv"


In [0]:
df_spark_transaction = spark.read.csv(usersCsvPath, sep=",", inferSchema=True, header=True)

df_spark_transaction.printSchema()

root
 |-- id: integer (nullable = true)
 |-- date: timestamp (nullable = true)
 |-- client_id: integer (nullable = true)
 |-- card_id: integer (nullable = true)
 |-- amount: string (nullable = true)
 |-- use_chip: string (nullable = true)
 |-- merchant_id: integer (nullable = true)
 |-- merchant_city: string (nullable = true)
 |-- merchant_state: string (nullable = true)
 |-- zip: double (nullable = true)
 |-- mcc: integer (nullable = true)
 |-- errors: string (nullable = true)



In [0]:
end_time_extraction = time.time()
execution_time_extraction = end_time_extraction - start_time_extraction
print(f"Tempo total de execução: {execution_time_extraction:.2f} segundos")

Tempo total de execução: 46.98 segundos


#### 2 Tratamento de dados

In [0]:
#contagem tempo de execução da  transformação
start_time_transform = time.time()

In [0]:
df_spark_transaction_bronze = df_spark_transaction

In [0]:
df_spark_transaction_bronze = df_spark_transaction_bronze.withColumn("zip", col("zip").cast("integer"))
df_spark_transaction_bronze = df_spark_transaction_bronze.withColumn("zip", col("zip").cast("string"))

In [0]:
df_spark_transaction_bronze.createOrReplaceTempView('transactions')

In [0]:
df_spark_transaction_bronze = spark.sql('''
                               SELECT *,REPLACE(amount, '$', '') AS amount_dollar
                               FROM transactions;
                               ''')
df_spark_transaction_bronze = df_spark_transaction_bronze.drop('amount')
df_spark_transaction_bronze = df_spark_transaction_bronze.withColumn("amount_dollar", col("amount_dollar").cast("double"))    
df_spark_transaction_bronze = df_spark_transaction_bronze.drop('errors')

In [0]:
df_spark_transaction_bronze = df_spark_transaction_bronze.fillna({"merchant_state": "WEB"})
df_spark_transaction_bronze = df_spark_transaction_bronze.fillna({"zip": 0})

In [0]:
df_spark_transaction_silver = df_spark_transaction_bronze

In [0]:
df_spark_transaction_silver.display()

id date client_id card_id use_chip merchant_id merchant_city merchant_state zip mcc amount_dollar 7475327 2010-01-01T00:01:00.000+0000 1556 2972 Swipe Transaction 59935 Beulah ND 58523 5499 -77.0 7475328 2010-01-01T00:02:00.000+0000 561 4575 Swipe Transaction 67570 Bettendorf IA 52722 5311 14.57 7475329 2010-01-01T00:02:00.000+0000 1129 102 Swipe Transaction 27092 Vista CA 92084 4829 80.0 7475331 2010-01-01T00:05:00.000+0000 430 2860 Swipe Transaction 27092 Crown Point IN 46307 4829 200.0 7475332 2010-01-01T00:06:00.000+0000 848 3915 Swipe Transaction 13051 Harwood MD 20776 5813 46.41 7475333 2010-01-01T00:07:00.000+0000 1807 165 Swipe Transaction 20519 Bronx NY 10464 5942 4.81 7475334 2010-01-01T00:09:00.000+0000 1556 2972 Swipe Transaction 59935 Beulah ND 58523 5499 77.0 7475335 2010-01-01T00:14:00.000+0000 1684 2140 Online Transaction 39021 ONLINE WEB 0 4784 26.46 7475336 2010-01-01T00:21:00.000+0000 335 5131 Online Transaction 50292 ONLINE WEB 0 7801 261.58 7475337 2010-01-01T00:21:00.000+0000 351 1112 Swipe Transaction 3864 Flushing NY 11355 5813 10.74 7475338 2010-01-01T00:23:00.000+0000 554 3912 Swipe Transaction 67570 Pearland TX 77581 5311 3.51 7475339 2010-01-01T00:23:00.000+0000 605 5061 Swipe Transaction 75781 Brooklyn NY 11210 5411 2.58 7475340 2010-01-01T00:26:00.000+0000 1556 2972 Swipe Transaction 59935 Beulah ND 58523 5499 39.63 7475341 2010-01-01T00:27:00.000+0000 1797 1127 Swipe Transaction 33326 Kahului HI 96732 4121 43.33 7475342 2010-01-01T00:30:00.000+0000 114 3398 Swipe Transaction 61195 North Hollywood CA 91606 5541 49.42 7475343 2010-01-01T00:31:00.000+0000 1634 2464 Swipe Transaction 20519 San Benito TX 78586 5942 1.09 7475344 2010-01-01T00:32:00.000+0000 646 2093 Swipe Transaction 1636 Erie PA 16511 7538 73.79 7475345 2010-01-01T00:32:00.000+0000 1129 5492 Swipe Transaction 27092 Vista CA 92084 4829 100.0 7475346 2010-01-01T00:34:00.000+0000 394 4717 Online Transaction 39021 ONLINE WEB 0 4784 26.04 7475347 2010-01-01T00:36:00.000+0000 114 3398 Swipe Transaction 61195 North Hollywood CA 91606 5541 -64.0 7475348 2010-01-01T00:36:00.000+0000 1376 2182 Swipe Transaction 88945 Cedar Park TX 78613 5813 54.27 7475349 2010-01-01T00:37:00.000+0000 1682 238 Swipe Transaction 21586 Grand Forks ND 58201 5411 20.74 7475350 2010-01-01T00:38:00.000+0000 114 3398 Swipe Transaction 61195 North Hollywood CA 91606 5541 64.0 7475351 2010-01-01T00:38:00.000+0000 121 5952 Swipe Transaction 11901 Menasha WI 54952 5300 57.54 7475353 2010-01-01T00:43:00.000+0000 301 3742 Online Transaction 39021 ONLINE WEB 0 4784 10.17 7475354 2010-01-01T00:43:00.000+0000 1755 4228 Swipe Transaction 28666 Cordele GA 31015 5921 12.01 7475356 2010-01-01T00:45:00.000+0000 566 3439 Online Transaction 16798 ONLINE WEB 0 4121 16.86 7475357 2010-01-01T00:46:00.000+0000 379 3881 Swipe Transaction 50783 Mobile AL 36695 5411 4.64 7475358 2010-01-01T00:48:00.000+0000 401 3004 Swipe Transaction 68977 West Covina CA 91791 3174 669.88 7475359 2010-01-01T00:48:00.000+0000 1127 3869 Online Transaction 39021 ONLINE WEB 0 4784 22.57 7475360 2010-01-01T00:49:00.000+0000 652 4293 Swipe Transaction 74624 East Hartford CT 6108 5411 2.4 7475361 2010-01-01T00:53:00.000+0000 1963 3317 Swipe Transaction 69972 Vacaville CA 95687 5814 40.35 7475362 2010-01-01T00:56:00.000+0000 1357 4488 Swipe Transaction 78632 Tacoma WA 98404 5921 14.57 7475363 2010-01-01T00:57:00.000+0000 285 3442 Swipe Transaction 81536 Watsonville CA 95076 5310 7.8 7475364 2010-01-01T00:57:00.000+0000 1201 16 Swipe Transaction 61195 Woburn MA 1801 5541 2.95 7475365 2010-01-01T01:01:00.000+0000 820 127 Online Transaction 73186 ONLINE WEB 0 4814 270.22 7475366 2010-01-01T01:03:00.000+0000 1703 2969 Swipe Transaction 43293 Grand Junction CO 81506 5499 78.0 7475367 2010-01-01T01:06:00.000+0000 1758 4686 Online Transaction 17976 ONLINE WEB 0 4900 87.09 7475368 2010-01-01T01:07:00.000+0000 414 2815 Swipe Transaction 5258 Morristown NJ 7960 4900 148.39 7475370 2010-01-01T01:07:00.000+0000 1963 3364 Swipe 

In [0]:
end_time_transform = time.time()
execution_time_transform = end_time_transform - start_time_transform
print(f"Tempo total de execução: {execution_time_transform:.2f} segundos")

Tempo total de execução: 1.72 segundos


#### 3. Armazenamento de dados

In [0]:
# Inicializar controle de tempos
tempos_execucao = {"transacoes": {}, "cartoes": {}, "usuarios": {}}


In [0]:
# Extração dos arquivos para DataFrames Spark
# Função para medir o tempo
def medir_tempo_extracao(nome, caminho):
    start_time = time.time()
    df = spark.read.csv(caminho, header=True, inferSchema=True)
    end_time = time.time()
    tempo = end_time - start_time
    print(f"Tempo total da extração do dataset de {nome}: {tempo:.2f} segundos")
    return df, tempo

# Extraindo dados
df_transacoes, tempos_execucao["transacoes"]["extracao"] = medir_tempo_extracao("transações", "dbfs:/FileStore/transactions_data.csv")
df_cartoes, tempos_execucao["cartoes"]["extracao"] = medir_tempo_extracao("cartões", "dbfs:/FileStore/cards_data.csv")
df_usuarios, tempos_execucao["usuarios"]["extracao"] = medir_tempo_extracao("usuários", "dbfs:/FileStore/users_data.csv")

Tempo total da extração do dataset de transações: 45.61 segundos
Tempo total da extração do dataset de cartões: 0.83 segundos
Tempo total da extração do dataset de usuários: 0.65 segundos


In [0]:
# Exemplo de transformação (adicionando colunas calculadas como exemplo)
def transformar_dados(df, nome):
    start_time = time.time()
    df_transformado = df.withColumnRenamed("user_id", "id_usuario")  # Exemplo de transformação
    end_time = time.time()
    tempo = end_time - start_time
    print(f"Tempo total da transformação do dataset de {nome}: {tempo:.2f} segundos")
    return df_transformado, tempo

df_transacoes_transformado, tempos_execucao["transacoes"]["transformacao"] = transformar_dados(df_transacoes, "transações")
df_cartoes_transformado, tempos_execucao["cartoes"]["transformacao"] = transformar_dados(df_cartoes, "cartões")
df_usuarios_transformado, tempos_execucao["usuarios"]["transformacao"] = transformar_dados(df_usuarios, "usuários")


Tempo total da transformação do dataset de transações: 0.00 segundos
Tempo total da transformação do dataset de cartões: 0.00 segundos
Tempo total da transformação do dataset de usuários: 0.00 segundos


In [0]:
# Carga dos arquivos transformados para Parquet
def salvar_parquet(df, caminho, nome):
    start_time = time.time()
    df.write.mode("overwrite").parquet(caminho)
    end_time = time.time()
    tempo = end_time - start_time
    print(f"Tempo total da carga do dataset de {nome}: {tempo:.2f} segundos")
    return tempo

tempos_execucao["transacoes"]["carga"] = salvar_parquet(df_transacoes_transformado, "dbfs:/FileStore/Tabela_Transacoes_Silver", "transações")
tempos_execucao["cartoes"]["carga"] = salvar_parquet(df_cartoes_transformado, "dbfs:/FileStore/Tabela_Cartoes_Silver", "cartões")
tempos_execucao["usuarios"]["carga"] = salvar_parquet(df_usuarios_transformado, "dbfs:/FileStore/Tabela_Usuarios_Silver", "usuários")

Tempo total da carga do dataset de transações: 101.80 segundos
Tempo total da carga do dataset de cartões: 1.59 segundos
Tempo total da carga do dataset de usuários: 1.30 segundos


In [0]:
import pandas as pd

df_tempo_execucao = pd.DataFrame(tempos_execucao).T
print(df_tempo_execucao)

             extracao  transformacao       carga
transacoes  45.609710       0.003376  101.800351
cartoes      0.834878       0.002986    1.585120
usuarios     0.645514       0.003077    1.295790
